<a href="https://colab.research.google.com/github/lygitdata/GarmentIQ/blob/gh-pages/lygitdata/classification/main.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Import Libraries and Set Seed

In [1]:
import pandas as pd
import numpy as np
import os
import math
import shutil
import random
from sklearn.model_selection import train_test_split, StratifiedKFold
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import Dataset, DataLoader, Subset
from torchvision import transforms
from PIL import Image
import torch.nn.functional as F
from tqdm.notebook import tqdm

# Set all seeds for reproducibility
SEED = 88
random.seed(SEED)
np.random.seed(SEED)
torch.manual_seed(SEED)
torch.cuda.manual_seed_all(SEED)
torch.backends.cudnn.deterministic = True
torch.backends.cudnn.benchmark = False
max_workers = min(os.cpu_count(), 8)

# Improt and Preprocess Data

In [2]:
# Load the dataset
apparel = pd.read_csv('/content/drive/MyDrive/dsl/classification/apparel.csv')

# Split into train and test sets
X = apparel['id']
y = apparel['articleType']
X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.1, stratify=y, random_state=SEED
)
train_df = pd.DataFrame({'id': X_train, 'articleType': y_train}).reset_index(drop=True)
test_df = pd.DataFrame({'id': X_test, 'articleType': y_test}).reset_index(drop=True)

In [3]:
!unzip -q /content/drive/MyDrive/dsl/classification/valid_images.zip -d /content

In [4]:
# Create directories
valid_images_dir = '/content/valid_images/'
train_set_dir = '/content/train_set/'
test_set_dir = '/content/drive/MyDrive/dsl/classification/test_set/'
os.makedirs(train_set_dir, exist_ok=True)
os.makedirs(test_set_dir, exist_ok=True)

# Move images to appropriate directories
def move_images(df, target_dir):
    for img_id in df['id']:
        src = os.path.join(valid_images_dir, f"{img_id}.jpg")
        dst = os.path.join(target_dir, f"{img_id}.jpg")
        if os.path.exists(src):
            shutil.move(src, dst)
        else:
            print(f"Warning: {src} not found.")

move_images(train_df, train_set_dir)
move_images(test_df, test_set_dir)

In [5]:
# Define the dataset class
class MemoryApparelDataset(Dataset):
    def __init__(self, df, img_dir, transform=None):
        self.df = df
        self.transform = transform
        self.classes = sorted(df['articleType'].unique())
        self.class_to_idx = {c: i for i, c in enumerate(self.classes)}

        # Preload all images into memory
        self.images, self.labels = self._preload_images(img_dir)

    def _preload_images(self, img_dir):
        images = []
        labels = []
        print(f"Preloading {len(self.df)} images into memory...")

        for idx in tqdm(range(len(self.df)), desc='Loading'):
            row = self.df.iloc[idx]
            img_path = os.path.join(img_dir, f"{row['id']}.jpg")

            try:
                # Load and transform once during initialization
                image = Image.open(img_path).convert('RGB')
                if self.transform:
                    image = self.transform(image)
                images.append(image)
                labels.append(self.class_to_idx[row['articleType']])
            except Exception as e:
                print(f"Skipping corrupted image {img_path}: {str(e)}")
                continue

        return images, labels

    def __len__(self):
        return len(self.images)

    def __getitem__(self, idx):
        # Direct memory access during training
        return self.images[idx], self.labels[idx]

# Model Preparation

In [6]:
# Define transforms
preload_transform = transforms.Compose([
    transforms.Resize((60, 80)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])

In [7]:
# Define the CNN model
class CNN(nn.Module):
    def __init__(self, num_classes=5):
        super(CNN, self).__init__()
        self.features = nn.Sequential(
            # Block 1
            nn.Conv2d(3, 64, kernel_size=3, padding=1),
            nn.BatchNorm2d(64),
            nn.ReLU(inplace=True),
            nn.Conv2d(64, 64, kernel_size=3, padding=1),
            nn.BatchNorm2d(64),
            nn.ReLU(inplace=True),
            nn.MaxPool2d(2, 2),
            nn.Dropout(0.25),

            # Block 2
            nn.Conv2d(64, 128, kernel_size=3, padding=1),
            nn.BatchNorm2d(128),
            nn.ReLU(inplace=True),
            nn.Conv2d(128, 128, kernel_size=3, padding=1),
            nn.BatchNorm2d(128),
            nn.ReLU(inplace=True),
            nn.MaxPool2d(2, 2),
            nn.Dropout(0.25),

            # Block 3
            nn.Conv2d(128, 256, kernel_size=3, padding=1),
            nn.BatchNorm2d(256),
            nn.ReLU(inplace=True),
            nn.Conv2d(256, 256, kernel_size=3, padding=1),
            nn.BatchNorm2d(256),
            nn.ReLU(inplace=True),
            nn.AdaptiveAvgPool2d((4, 6))
        )

        self.classifier = nn.Sequential(
            nn.Linear(256 * 4 * 6, 512),
            nn.BatchNorm1d(512),
            nn.ReLU(inplace=True),
            nn.Dropout(0.5),
            nn.Linear(512, 256),
            nn.BatchNorm1d(256),
            nn.ReLU(inplace=True),
            nn.Dropout(0.3),
            nn.Linear(256, num_classes)
        )

    def forward(self, x):
        x = self.features(x)
        x = x.view(x.size(0), -1)
        x = self.classifier(x)
        return x

In [8]:
# Check for GPU availability
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

# Variables to track the best model
overall_best_loss = float('inf')
best_model_path = '/content/drive/MyDrive/dsl/classification/model.pth'

# Prepare cross-validation
kfold = StratifiedKFold(n_splits=10, shuffle=True, random_state=SEED)

# Define worker init function for DataLoader reproducibility
def seed_worker(worker_id):
    worker_seed = SEED + worker_id
    random.seed(worker_seed)
    np.random.seed(worker_seed)
    torch.manual_seed(worker_seed)

# Model Training

In [9]:
# Preload ALL training data once before cross-validation
full_train_dataset = MemoryApparelDataset(train_df, train_set_dir, transform=preload_transform)

# Store in list for memory persistence
cached_images = [img for img in full_train_dataset.images]
cached_labels = [label for label in full_train_dataset.labels]

class CachedDataset(Dataset):
    def __init__(self, indices):
        self.indices = indices

    def __len__(self):
        return len(self.indices)

    def __getitem__(self, idx):
        actual_idx = self.indices[idx]
        return cached_images[actual_idx], cached_labels[actual_idx]

Preloading 13362 images into memory...


Loading:   0%|          | 0/13362 [00:00<?, ?it/s]

In [10]:
for fold, (train_idx, val_idx) in enumerate(kfold.split(train_df, train_df['articleType'])):
    print(f"Fold {fold + 1}/10")

    # Create cached datasets using preloaded data
    train_dataset = CachedDataset(train_idx)
    val_dataset = CachedDataset(val_idx)

    batch_size = 128
    g = torch.Generator()
    g.manual_seed(SEED)

    train_loader = DataLoader(
        train_dataset,
        batch_size=batch_size,
        shuffle=True,
        num_workers=max_workers,
        worker_init_fn=seed_worker,
        generator=g,
        pin_memory=True,
        persistent_workers=True
    )
    val_loader = DataLoader(
        val_dataset,
        batch_size=batch_size,
        shuffle=False,
        num_workers=max_workers,
        worker_init_fn=seed_worker,
        generator=g,
        pin_memory=True,
        persistent_workers=True
    )

    # Initialize model, optimizer, loss
    model = CNN(num_classes=5).to(device)
    model = nn.DataParallel(model)
    torch.cuda.empty_cache()
    criterion = nn.CrossEntropyLoss()
    optimizer = optim.Adam(model.parameters(), lr=0.0005)

    best_fold_loss = float('inf')
    patience = 10
    patience_counter = 0
    epoch_pbar = tqdm(range(100), desc="Total Progress", leave=False)

    for epoch in epoch_pbar:
        # Training phase with progress bar
        model.train()
        running_loss = 0.0
        train_pbar = tqdm(train_loader, desc=f"Epoch {epoch+1} Training", leave=False)

        for images, labels in train_pbar:
            images, labels = images.to(device, non_blocking=True), labels.to(device, non_blocking=True)
            optimizer.zero_grad()
            outputs = model(images)
            loss = criterion(outputs, labels)
            loss.backward()
            optimizer.step()

            running_loss += loss.item() * images.size(0)
            train_pbar.set_postfix({'batch_loss': f"{loss.item():.4f}"})

        epoch_loss = running_loss / len(train_loader.dataset)

        # Validation phase with progress bar
        model.eval()
        val_loss = 0.0
        val_pbar = tqdm(val_loader, desc=f"Epoch {epoch+1} Validation", leave=False)

        with torch.no_grad():
            for images, labels in val_pbar:
                images, labels = images.to(device), labels.to(device)
                outputs = model(images)
                loss = criterion(outputs, labels)
                val_loss += loss.item() * images.size(0)
                val_pbar.set_postfix({'val_batch_loss': f"{loss.item():.4f}"})

        val_loss /= len(val_loader.dataset)

        if val_loss < best_fold_loss:
            best_fold_loss = val_loss
            patience_counter = 0  # Reset counter when improvement
            torch.save(model.state_dict(), f'/content/drive/MyDrive/dsl/classification/model/fold_{fold}_best.pth')
        else:
            patience_counter += 1  # Increment when no improvement

        # Update overall best model
        if val_loss < overall_best_loss:
            overall_best_loss = val_loss
            torch.save(model.state_dict(), best_model_path)

        # Early stopping check
        epoch_pbar.set_postfix({
            'train_loss': f"{epoch_loss:.4f}",
            'val_loss': f"{val_loss:.4f}",
            'patience': patience_counter
        })

        if patience_counter >= patience:
            print(f"\nEarly stopping at epoch {epoch+1}")
            break

print("Training completed. Best model saved at:", best_model_path)

Fold 1/10


Total Progress:   0%|          | 0/100 [00:00<?, ?it/s]

Epoch 1 Training:   0%|          | 0/94 [00:00<?, ?it/s]

Epoch 1 Validation:   0%|          | 0/11 [00:00<?, ?it/s]

Epoch 2 Training:   0%|          | 0/94 [00:00<?, ?it/s]

...

Epoch 19 Training:   0%|          | 0/94 [00:00<?, ?it/s]

Epoch 19 Validation:   0%|          | 0/11 [00:00<?, ?it/s]

Epoch 20 Training:   0%|          | 0/94 [00:00<?, ?it/s]

Epoch 20 Validation:   0%|          | 0/11 [00:00<?, ?it/s]


Early stopping at epoch 20
Training completed. Best model saved at: /content/drive/MyDrive/dsl/classification/model.pth


# Model Performance on Test Set

In [21]:
from sklearn.metrics import f1_score, accuracy_score, classification_report

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model = CNN(num_classes=5).to(device)

state_dict = torch.load(
    '/content/drive/MyDrive/dsl/classification/model.pth',
    map_location=device,
    weights_only=True
)

# Remove 'module.' prefix from keys
new_state_dict = {k.replace('module.', ''): v for k, v in state_dict.items()}

# Load into model
model.load_state_dict(new_state_dict, strict=False)
model.eval()

# Define test dataset class
class TestDataset(Dataset):
    def __init__(self, df, img_dir, transform=None):
        self.df = df
        self.img_dir = img_dir
        self.transform = transform
        self.classes = sorted(['Shirts', 'Pants', 'Tops', 'Kurtas', 'Shorts'])  # Match training class order
        self.class_to_idx = {c: i for i, c in enumerate(self.classes)}

    def __len__(self):
        return len(self.df)

    def __getitem__(self, idx):
        row = self.df.iloc[idx]
        img_path = os.path.join(self.img_dir, f"{row['id']}.jpg")
        image = Image.open(img_path).convert('RGB')
        label = self.class_to_idx[row['articleType']]
        if self.transform:
            image = self.transform(image)
        return image, label

# Define transforms
transform = transforms.Compose([
    transforms.Resize((60, 80)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])

# Create test dataset and loader
test_dataset = TestDataset(test_df, test_set_dir, transform=transform)
test_loader = DataLoader(test_dataset, batch_size=64, shuffle=False, num_workers=2)

# Evaluation
all_preds = []
all_labels = []
total_loss = 0.0
criterion = nn.CrossEntropyLoss()

with torch.no_grad():
    for images, labels in tqdm(test_loader, desc="Evaluating"):
        images = images.to(device)
        labels = labels.to(device)

        outputs = model(images)
        loss = criterion(outputs, labels)

        total_loss += loss.item() * images.size(0)
        _, preds = torch.max(outputs, 1)

        all_preds.extend(preds.cpu().numpy())
        all_labels.extend(labels.cpu().numpy())

# Calculate metrics
test_loss = total_loss / len(test_loader.dataset)
test_acc = accuracy_score(all_labels, all_preds)
test_f1 = f1_score(all_labels, all_preds, average='weighted')

print(f"Test Loss: {test_loss:.4f}")
print(f"Test Accuracy: {test_acc:.4f}")
print(f"Test F1 Score: {test_f1:.4f}")
print("\nClassification Report:")
print(classification_report(all_labels, all_preds, target_names=test_dataset.classes))

Evaluating:   0%|          | 0/24 [00:00<?, ?it/s]

Test Loss: 0.1785
Test Accuracy: 0.9374
Test F1 Score: 0.9336

Classification Report:
              precision    recall  f1-score   support

      Kurtas       0.96      0.98      0.97       174
       Pants       0.95      0.99      0.97       109
      Shirts       0.94      0.98      0.96       982
      Shorts       0.96      0.87      0.91        52
        Tops       0.86      0.62      0.72       168

    accuracy                           0.94      1485
   macro avg       0.93      0.89      0.91      1485
weighted avg       0.93      0.94      0.93      1485

